# Clinical Trial Optimization 

Je presente ici ma solution pour le probléme d'opimisation d'un trie de sujet pour un test clinique.

### Presentation du probléme

Cette compétition organisée par Ingenii portait sur l'optimisation du tri des sujets pour un essai clinique. La description complète du problème est disponible sur [la plateforme Aqora](https://aqora.io/competitions/ingenii-clinical-trial), qui héberge la compétition.

Le problème consiste à regrouper les sujets en fonction de certains paramètres lors d'un essai clinique. L'objectif est qu'à l'issue de la formation des groupes, les sujets d'un même groupe soient adaptés aux tests cliniques qu'ils devront subir.

### Formulation mathématique

Nous avons 100 sujets que nous souhaitons répartir en deux groupes $p = \{1, 2\}$ de 50 personnes chacun. Chaque sujet $i$ est caractérisé par 3 paramètres $\vec{w_i} = (w_{i1}, w_{i2}, w_{i3})$. Nous mesurons la qualité de ce partitionnement à l'aide de la grandeur suivante :

$$
d = \sum_{s=1}^{3} |\Delta\mu_s| + \rho \sum_{s=1}^{3} |\Delta\sigma_{ss}| + 2\rho \sum_{s=1}^{3} \sum_{s' = s+1}^{3} |\Delta\sigma_{ss'}|
$$

où :

$$
\Delta\mu_s = \frac{1}{n} \sum_{i=1}^{n} w_{is}(x_{i1} - x_{i2})
$$

et :

$$
\Delta\sigma_{ss'} = \frac{1}{n} \sum_{i=1}^{n} w_{is} w_{is'} (x_{i1} - x_{i2})
$$

$x_{ip}$ est une variable binaire qui vaut 1 si le sujet $i$ appartient au groupe $p$, et 0 sinon.

La grandeur $d$ est appelée la *discrepancy*. Pour un regroupement idéal, la *discrepancy* est minimale. Ce problème de regroupement se ramène donc à résoudre le problème d'optimisation suivant :

$$
\min_{x} d
$$

sous les contraintes :

$$
\sum_{i}x_{ip} = \frac{n}{2}, \quad \text{Chaque groupe contient le même nombre de sujets.}
$$

$$
x_{i1} + x_{i2} = 1, \quad \text{Un sujet ne peut appartenir qu'à un seul groupe après le regroupement.}
$$

$$
x_{12} = 0, \quad \text{Ceci pour éviter la redondance des solutions, car on obtient le même regroupement en intervertissant les groupes 1 et 2.}
$$

### Reformulation du problème

Dans sa formulation initiale, le problème semble nous orienter vers l'utilisation de l'algorithme QAOA. Cependant, cette formulation ne permet pas une implémentation directe de l'algorithme en raison de la présence de valeurs absolues dans la fonction objective. De plus, le nombre de variables impliquées est très élevé : on a effectivement $2n-1$ variables, soit 199 variables dans ce cas, ce qui nécessiterait au moins une machine de 199 qubits, ce qui n'est actuellement pas disponible.

* **Écriture sans valeurs absolues :**
$$ a = |x| \Rightarrow x \leq a \text{ et } -x \leq a$$

Nous posons alors $z_s = |\Delta\mu_s|$, $z_{ss} = |\Delta\sigma_{ss}|$, et $z_{ss'} = |\Delta\sigma_{ss'}|$. La nouvelle formulation devient :
$$
\min_{x, z} \sum_{s=1}^{3} z_s + \rho \sum_{s=1}^{3} z_{ss} + 2\rho \sum_{s=1}^{3} \sum_{s' = s+1}^{3} z_{ss'}
$$
sous les contraintes suivantes :
$$
\sum_{i} x_{ip} = \frac{n}{2}, \quad \text{chaque groupe contient le même nombre de sujets.}
$$
$$
x_{i1} + x_{i2} = 1, \quad \text{un sujet ne peut appartenir qu'à un seul groupe après le regroupement.}
$$
$$
x_{12} = 0, \quad \text{cela évite la redondance des solutions, car intervertir les groupes 1 et 2 donnerait le même regroupement.}
$$
$$
\Delta\mu_s \leq z_s \text{ et } -\Delta\mu_s \leq z_s
$$
$$
\Delta\sigma_{ss} \leq z_{ss} \text{ et } -\Delta\sigma_{ss} \leq z_{ss}
$$
$$
\Delta\sigma_{ss'} \leq z_{ss'} \text{ et } -\Delta\sigma_{ss'} \leq z_{ss'}
$$

* **Réduction du nombre de variables :**

En remplaçant la contrainte $x_{i1} + x_{i2} = 1$ dans le problème, nous réduisons de $n$ le nombre de variables. En ajoutant les variables $z$, nous obtenons finalement $n - 1 + 9$, soit $n + 8$ variables.

# Implémentation
À ce stade, le problème est bien défini pour être implémenté avec l'algorithme QAOA. La prochaine étape consiste à le transformer en un problème QUBO, une transformation bien connue et générique. Cette étape sera réalisée à l'aide d'une bibliothèque dédiée de Qiskit.

In [1]:
from qiskit_optimization import QuadraticProgram

In [2]:
n =  100 #number of subjects
N = 1 # on enléve la division par 1 dans la fonction objective
rho = 0.5

In [3]:
import csv
import numpy as np

data_list_csv = []
with open('pbc.csv', mode='r') as file:
    reader = csv.reader(file)
    # Skip the header
    next(reader)
    # Iterate over the rows and add them to the list
    for row in reader:
        # Convert strings to float for numeric columns
        data_list_csv.append([float(row[0]), float(row[1]), float(row[2])])

# je prend un arrondi à deux chiffre apres la virgule et je multiplie toute les donnée par 100 
# Pour s'assuerer que tout les coéfficlents des contraintes soient entiére. ceci est 
# necessaire pour que le probléme soit convertible en QUBO. Cette transformation ne modifie pas la combin
max_values = np.max(data_list_csv , axis=0)
data_list_frmt = data_list_csv
#data_list_frmt = [[(np.around(val ,2)) for val in ligne] for ligne in data_list_csv]



In [4]:
print(data_list_frmt[:10])

[[12.2, 58.7652292950034, 1718.0], [10.6, 56.4462696783025, 7394.8], [12.0, 70.072553045859, 516.0], [10.3, 54.7405886379192, 6121.8], [10.9, 38.1054072553046, 671.0], [11.0, 66.258726899384, 944.0], [9.7, 55.5345653661875, 824.0], [11.0, 53.056810403833, 4651.2], [11.0, 42.507871321013, 2276.0], [11.5, 70.5598904859685, 918.0]]


In [5]:
mod = QuadraticProgram("Clinical trial Optimization")

for i in range(1 , n + 1):
    var_name = f"x_{i}1"
    mod.binary_var(name=var_name)

# Variables entiere   
W = []
for i in range(3):
    w_list = [row[i] for row in data_list_frmt]
    w_sum = 0
    for w in w_list:
        w_sum = w_sum + w # Somme des w
    W.append(w_sum)

mod.integer_var(name= "z_1" , lowerbound=0 , upperbound= int(W[0]) + 1)
mod.integer_var(name= "z_2" , lowerbound=0 , upperbound= int(W[1]) + 1)
mod.integer_var(name= "z_3" , lowerbound=0 , upperbound= int(W[2]) + 1)
#mod.continuous_var(name = "z_1" , lowerbound=0 , upperbound=int(W[0]) + 1)
#mod.continuous_var(name = "z_2" , lowerbound=0 , upperbound=int(W[1]) + 1)
#mod.continuous_var(name = "z_3" , lowerbound=0 , upperbound=int(W[2]) + 1)

W_square = []
for i in range(3):
    w_list = [row[i] for row in data_list_frmt]
    w_sum = 0
    for w in w_list:
        w_sum = w_sum + w**2 # somme des w au carré
    W_square.append(w_sum)

mod.integer_var(name= "z_11" , lowerbound=0 , upperbound= int(W_square[0]) + 1)
mod.integer_var(name= "z_22" , lowerbound=0 , upperbound= int(W_square[1]) + 1)
mod.integer_var(name= "z_33" , lowerbound=0 , upperbound= int(W_square[2]) + 1)
#mod.continuous_var(name="z_11" , lowerbound=0 , upperbound=int(W_square[0]) + 1)
#mod.continuous_var(name="z_22" , lowerbound=0 , upperbound=int(W_square[1]) + 1)
#mod.continuous_var(name="z_33" , lowerbound=0 , upperbound=int(W_square[2]) + 1)


W_cross = []
for i in range(3):
    w_list_s = [row[i] for row in data_list_frmt]
    for k in range(i + 1, 3):
        w_sum = 0
        w_list_s_prime = [row[k] for row in data_list_frmt]
        for w_i, w_k in zip(w_list_s, w_list_s_prime):  
            w_sum = w_sum + w_i * w_k # somme des produit croisé de w
        W_cross.append(w_sum)
mod.integer_var(name = "z_12" , lowerbound=0 , upperbound=int(W_cross[0] + 1))
mod.integer_var(name = "z_13" , lowerbound=0 , upperbound=int(W_cross[1] + 1))
mod.integer_var(name = "z_23" , lowerbound=0 , upperbound=int(W_cross[2] + 1))
#mod.continuous_var(name="z_12" , lowerbound=0 , upperbound=int(W_cross[0]) + 1)
#mod.continuous_var(name="z_13" , lowerbound=0 , upperbound=int(W_cross[1]) + 1)
#mod.continuous_var(name="z_23" , lowerbound=0 , upperbound=int(W_cross[2]) + 1)



<Variable: 0 <= z_23 <= 30608403 (integer)>

In [6]:
# definition de la fonction objective
mod.minimize(linear={"z_1": 1 ,"z_2": 1 , "z_3": 1 
                      , "z_11":0.5 , "z_22":0.5 , "z_33":0.5
                      , "z_12":1 , "z_13":1 , "z_23":1})

# Les contraintes

Contraite $ \sum_{i} x_{ip} = \frac{n}{2} \text{ avec } p = 1$

In [7]:
dict_som = {f"x_{i}1": 1 for i in range(1 , n + 1)}
mod.linear_constraint(dict_som , sense= "==" , rhs = n/2 , name = "repartition egale")

<LinearConstraint: x_1001 + x_101 + x_11 + x_111 + x_121 + x_131 + x_... == 50.0 'repartition egale'>

Contrainte: $x_{12} = 0 \Rightarrow x_{11} = 1$

In [8]:
mod.linear_constraint({"x_11": 1} , sense= "==" , rhs = 1 , name= "avoid redundance")

<LinearConstraint: x_11 == 1 'avoid redundance'>

Contrainte: $\Delta\mu_s \leq z_s \text{ et } -\Delta\mu_s \leq z_s$

$$
\Delta\mu_s \leq z_s  \Rightarrow \sum_{i = 1}^{n}2w_{is}x_{i1} - nz_{s} \leq \sum_{i = 1}^{n}w_{is} \\

-\Delta\mu_s \leq z_s \Rightarrow \sum_{i = 1}^{n}2w_{is}x_{i1} + nz_{s} \geq \sum_{i = 1}^{n}w_{is} 
$$



In [9]:
for i in range(3):
    dict_x_s = {}
    w_list = [row[i] for row in data_list_frmt]

    # multipli toute l'équation par 100 pour avoir uniquement des coéfficients entiers
    dict_x_s = {f"x_{j + 1}1": int(round(2*w_list[j] , 2)*100)  for j in range(0 , n)} 
    dict_x_s.update({f"z_{i + 1}": -n * 100})
    mod.linear_constraint(linear=dict_x_s , sense= "<=" , rhs= int(round(W[i] , 2)*100))
    


for i in range(3):
    dict_x_s = {}
    w_list = [row[i] for row in data_list_frmt]
    dict_x_s = {f"x_{j + 1}1": int(round(2*w_list[j])*100)  for j in range(0 , n)}
    dict_x_s.update({f"z_{i + 1}": n*100})
    mod.linear_constraint(linear=dict_x_s , sense= ">=" , rhs= int(round(W[i] , 2)*100))
    

Contrainte: $\Delta\sigma_{ss} \leq z_{ss} \text{ et } -\Delta\sigma_{ss} \leq z_{ss}$

$$
\Delta\sigma_{ss} \leq z_{ss} \Rightarrow \sum_{i = 1}^{n}2w_{is}^2x_{i1} - nz_{ss}  \leq \sum_{i = 1}^{n}w_{is}^2 \\

- \Delta\sigma_{ss} \leq z_{ss} \Rightarrow \sum_{i = 1}^{n}2w_{is}^2x_{i1} + nz_{ss}  \geq \sum_{i = 1}^{n}w_{is}^2 
$$

In [10]:
for i in range(3):
    dict_x_s = {}
    w_list = [row[i] for row in data_list_frmt]
    dict_x_s = {f"x_{j + 1}1": int(round(2*(w_list[j]**2),2)*100) for j in range(0 , n)}
    dict_x_s.update({f"z_{i + 1}" + f"{i + 1}": -n*100})
    mod.linear_constraint(linear=dict_x_s , sense= "<=" , rhs= int(round(W_square[i],2)*100))
   


for i in range(3):
    dict_x_s = {}
    w_list = [row[i] for row in data_list_frmt]
    dict_x_s = {f"x_{j + 1}1": int(round(2*(w_list[j]**2),2)*100) for j in range(0 , n)}
    dict_x_s.update({f"z_{i + 1}" + f"{i + 1}": n*100})
    mod.linear_constraint(linear=dict_x_s , sense= ">=" , rhs= int(round(W_square[i] , 2)*100))
    

Containte: $\Delta\sigma_{ss'} \leq z_{ss'} \text{ et } -\Delta\sigma_{ss'} \leq z_{ss'}$

$$
\Delta\sigma_{ss'} \leq z_{ss'} \Rightarrow \sum_{i = 1}^{n}2w_{is}w_{is'}x_{i1} - nz_{ss'}  \leq \sum_{i = 1}^{n}w_{is}w_{is'} \\

- \Delta\sigma_{ss'} \leq z_{ss'} \Rightarrow \sum_{i = 1}^{n}2w_{is}w_{is'}x_{i1} + nz_{ss'}  \geq \sum_{i = 1}^{n}w_{is}w_{is'} 
$$

In [11]:
for i in range(3):
    w_list_s = [row[i] for row in data_list_frmt]
    for k in range(i + 1 , 3):
        dict_x_s = {}
        w_list_s_prime = [row[k] for row in data_list_frmt]
        dict_x_s = {f"x_{j + 1}1": int(round(2*(w_list_s[j]*w_list_s_prime[j]) , 2)*100) for j in range(0 , n)}
        dict_x_s.update({f"z_{i + 1}" + f"{k + 1}": -n*100})
        mod.linear_constraint(linear=dict_x_s , sense= "<=" , rhs= int(round(W_cross[i] , 2)*100))
        


for i in range(3):
    w_list_s = [row[i] for row in data_list_frmt]
    for k in range(i + 1 , 3):
        dict_x_s = {}
        w_list_s_prime = [row[k] for row in data_list_frmt]
        dict_x_s = {f"x_{j + 1}1": int(round(2*(w_list_s[j]*w_list_s_prime[j]) , 2)*100) for j in range(0 , n)}
        dict_x_s.update({f"z_{i + 1}" + f"{k + 1}": n*100})
        mod.linear_constraint(linear=dict_x_s , sense= ">=" , rhs= int(round(W_cross[i],2)*100))

In [12]:
print(mod.prettyprint())

Problem name: Clinical trial Optimization

Minimize
  z_1 + 0.5*z_11 + z_12 + z_13 + z_2 + 0.5*z_22 + z_23 + z_3 + 0.5*z_33

Subject to
  Linear constraints (20)
    x_1001 + x_101 + x_11 + x_111 + x_121 + x_131 + x_141 + x_151 + x_161
    + x_171 + x_181 + x_191 + x_201 + x_21 + x_211 + x_221 + x_231 + x_241
    + x_251 + x_261 + x_271 + x_281 + x_291 + x_301 + x_31 + x_311 + x_321
    + x_331 + x_341 + x_351 + x_361 + x_371 + x_381 + x_391 + x_401 + x_41
    + x_411 + x_421 + x_431 + x_441 + x_451 + x_461 + x_471 + x_481 + x_491
    + x_501 + x_51 + x_511 + x_521 + x_531 + x_541 + x_551 + x_561 + x_571
    + x_581 + x_591 + x_601 + x_61 + x_611 + x_621 + x_631 + x_641 + x_651
    + x_661 + x_671 + x_681 + x_691 + x_701 + x_71 + x_711 + x_721 + x_731
    + x_741 + x_751 + x_761 + x_771 + x_781 + x_791 + x_801 + x_81 + x_811
    + x_821 + x_831 + x_841 + x_851 + x_861 + x_871 + x_881 + x_891 + x_901
    + x_91 + x_911 + x_921 + x_931 + x_941 + x_951 + x_961 + x_971 + x_981
    + x_991 

# Transformation en QUBO

La conversion d'un problème en QUBO (Quadratic Unconstrained Binary Optimization) est un processus générique sur lequel je ne me suis pas attardé en profondeur, bien qu'il soit intéressant de s'intéresser à la manière la plus optimale de réaliser cette transformation. Dans ce travail, cette conversion sera effectuée à l'aide des outils proposés par Qiskit.

In [13]:
from qiskit_optimization.converters import QuadraticProgramToQubo

cto_qubo = QuadraticProgramToQubo().convert(mod)
print(cto_qubo.prettyprint())

Problem name: Clinical trial Optimization

Minimize
  1364145036.5*c10@int_slack@0^2 + 5456580146*c10@int_slack@0*c10@int_slack@1
  + 2793769034752.0*c10@int_slack@0*c10@int_slack@10
  + 5587538069504.0*c10@int_slack@0*c10@int_slack@11
  + 11175076139008.0*c10@int_slack@0*c10@int_slack@12
  + 22350152278016.0*c10@int_slack@0*c10@int_slack@13
  + 44700304556032.0*c10@int_slack@0*c10@int_slack@14
  + 89400609112064.0*c10@int_slack@0*c10@int_slack@15
  + 178801218224128.0*c10@int_slack@0*c10@int_slack@16
  + 357602436448256.0*c10@int_slack@0*c10@int_slack@17
  + 715204872896512.0*c10@int_slack@0*c10@int_slack@18
  + 1430409745793024.0*c10@int_slack@0*c10@int_slack@19
  + 10913160292.0*c10@int_slack@0*c10@int_slack@2
  + 2860819491586048.0*c10@int_slack@0*c10@int_slack@20
  + 5721638983172096.0*c10@int_slack@0*c10@int_slack@21
  + 1.1443277966344192e+16*c10@int_slack@0*c10@int_slack@22
  + 2.2886555932688384e+16*c10@int_slack@0*c10@int_slack@23
  + 4.577311186537677e+16*c10@int_slack@0*c10

### Mapping into Ising Problem

Lorsqu'on transforme un problème quadratique en QUBO (Quadratic Unconstrained Binary Optimization), on se rend compte du nombre exponentiellement élevé de variables binaires supplémentaires nécessaires pour cette conversion. Cela est dû aux contraintes d'inégalité. En effet, pour une contrainte du type $a_0x_0 + ... + a_nx_n \leq S$, il faut $\log_{2}(S) + 1$ variables binaires supplémentaire pour en faire une contraite sur l'égalité.

Dans notre cas, les seconds membres des contraintes d'inégalité sont au moins de l'ordre de $10^5$, ce qui nécessite au moins 18 variables supplémentaires par équation. Avec 18 équations, cela représente au moins 324 variables supplémentaires, ce qui rend le problème pratiquement incalculable.

Ainsi, en raison de la formulation en valeur absolue, des données mises en jeu dans ce problème, et des contraintes de formatage imposées par la librairie Qiskit, une approche directe pour résoudre ce problème devient inaccessible.

In [14]:
# hamiltonian , offset = cto_qubo.to_ising()
# print("Offset:", offset)
# print("Ising Hamiltonian:")
# print(str(qubitOp))

Nous allons essayer une autre approche. au lieu de trouver le minimun de d , nous allons chercher le minimun de 
$$
d' = \sum_{s=1}^{3} (\Delta\mu_s)^2 + \rho \sum_{s=1}^{3} (\Delta\sigma_{ss})^2 + 2\rho \sum_{s=1}^{3} \sum_{s' = s+1}^{3} (\Delta\sigma_{ss'})^2
$$

ceci sous les même contrainte que $d$. 

Ensuite nous allons utiliser ce mimum comme point initiale pour recherche le minimun de d en admétant que $d'_{min}$ est proche de $d_{min}$

$$
(\Delta\mu_s)^2 = \frac{1}{n^2} \left( \sum_{j = 1}^{n}\sum_{i = 1}^{n} w_{js}w_{is}(4x_{j1}x_{i1} - 2x_{j1} - 2x_{i1} + 1) \right) = \frac{4}{n^2}\sum_{j = 1}^{n}\sum_{i = 1}^{n}w_{js}w_{is}x_{j1}x_{i1} - \frac{4}{n^2}\sum_{j = 1}^{n}\sum_{i = 1}^{n}w_{js}w_{is}x_{i1} + \frac{1}{n^2}\sum_{j = 1}^{n}\sum_{i = 1}^{n}w_{js}w_{is}
$$

$$
(\Delta\sigma_{ss})^{2} = 
$$

$$
(\Delta\sigma_{ss'})^{2} = 
$$


$$
\left( \sum_{i=1}^{n} x_i \right)
$$

In [19]:
mod_2 = QuadraticProgram("Clinical trial Optimization")

mod_2.binary_var("x")
mod_2.binary_var("y")
mod_2.binary_var("z")

<Variable: z (binary)>

In [16]:
#mod_2.minimize(linear={"x": 1 ,"y": 1}.update({"x": -2 , "y": 3}))


In [17]:
# # Définir plusieurs dictionnaires partiels
# dict_1 = {"x": 1, "y": 2}
# dict_2 = {"x": -3, "y": 4}

# # Fusionner les dictionnaires en additionnant les valeurs pour les mêmes variables
# combined_dict = {key: dict_1.get(key, 0) + dict_2.get(key, 0) for key in set(dict_1) | set(dict_2)}

# # Minimiser la fonction avec le dictionnaire fusionné
# mod_2.minimize(linear=combined_dict)

# # Afficher le résultat
# print(mod_2.prettyprint())


In [21]:
from collections import defaultdict

# Fonction pour fusionner plusieurs dictionnaires en additionnant les valeurs
def merge_dicts(*dicts):
    merged = defaultdict(int)  # Initialise un dictionnaire avec des valeurs par défaut de 0
    for d in dicts:
        for key, value in d.items():
            merged[key] += value  # Ajoute la valeur correspondante à chaque clé
    return dict(merged)

# Exemple d'utilisation avec plusieurs dictionnaires
dict_1 = {"x": 1, "y": 2}
dict_2 = {"x": -3, "y": 4}
dict_3 = {"x": 5, "z": 3}

# Fusionner tous les dictionnaires
combined_dict = merge_dicts(dict_1, dict_2, dict_3)

# Minimiser la fonction avec le dictionnaire fusionné
mod_2.minimize(linear=combined_dict)

# Afficher le résultat
print(mod_2.prettyprint())


Problem name: Clinical trial Optimization

Minimize
  3*x + 6*y + 3*z

Subject to
  No constraints

  Binary variables (3)
    x y z

